# Importing

In [1]:
import ee
import geemap
import fiona
import time
import json
from pathlib import Path
import datetime
import numpy as np
from utils.gee import export_sar

# Authentication

In [2]:
ee.Authenticate()



Successfully saved authorization token.


In [3]:
ee.Initialize()

# Reading Location data

In [4]:
location_shape = Path("D:\\Ferrari\\Projects\\trans_fusion\\site1\\data\\shp\\location.shp")

In [5]:
with fiona.open(location_shape) as location:
    for feat in location:
        roi = ee.Geometry(feat['geometry'])
        center = feat['properties']['center']

In [6]:
center

'Point (-59.98953959 -7.10765019)'

In [7]:
map_view = geemap.Map(center=(-7.10765019, -59.98953959), zoom=8)
map_view


Map(center=[-7.10765019, -59.98953959], controls=(WidgetControl(options=['position', 'transparent_bg'], widget…

In [8]:
location = geemap.shp_to_ee(str(location_shape))
map_view.addLayer(location, {}, 'Location')

# Images dates

In [9]:
n_sar_images = 12
before_days = 31
d0 = datetime.datetime.strptime('2019-08-14', "%Y-%m-%d")
d1 = datetime.datetime.strptime('2020-07-31', "%Y-%m-%d")
d2 = datetime.datetime.strptime('2021-07-02', "%Y-%m-%d")
dt1 = (d1-d0).days + before_days
dt2 = (d2-d1).days + before_days

In [10]:
start_date = d0 - datetime.timedelta(days=before_days)
end_date = d2
print(f'Analyzed Period: {start_date.date()}:{end_date.date()}')
sar_collection = ee.ImageCollection('COPERNICUS/S1_GRD_FLOAT').filterDate(str(start_date.date()), str(end_date.date())).filterBounds(roi)

Analyzed Period: 2019-07-14:2021-07-02


In [11]:
vizParams = {
  'bands': ['VV', 'VH']
}

In [12]:
ds = np.arange(dt1)
img_collections = []
split_ds = np.array_split(ds, 12)
for i, dsi in enumerate(split_ds):
    di0 = d0 - datetime.timedelta(days=before_days) + datetime.timedelta(days=int(dsi[0]))
    di1 = d0 - datetime.timedelta(days=before_days) + datetime.timedelta(days=int(dsi[-1]))
    img_col = sar_collection.filterDate(str(di0.date()), str(di1.date()))
    img = img_col.mean().clip(roi)
    print(f'{di0}-{di1}-delta:{(di1-di0).days}|{len(img_col.getInfo()["features"])} images')
    map_view.addLayer(img, vizParams, f't1-{i:04d}')
    export_sar(img, roi, f't1_{i:04d}')

2019-07-14 00:00:00-2019-08-14 00:00:00-delta:31|6 images
2019-08-15 00:00:00-2019-09-15 00:00:00-delta:31|10 images
2019-09-16 00:00:00-2019-10-17 00:00:00-delta:31|12 images
2019-10-18 00:00:00-2019-11-18 00:00:00-delta:31|11 images
2019-11-19 00:00:00-2019-12-20 00:00:00-delta:31|9 images
2019-12-21 00:00:00-2020-01-21 00:00:00-delta:31|12 images
2020-01-22 00:00:00-2020-02-22 00:00:00-delta:31|10 images
2020-02-23 00:00:00-2020-03-25 00:00:00-delta:31|14 images
2020-03-26 00:00:00-2020-04-26 00:00:00-delta:31|18 images
2020-04-27 00:00:00-2020-05-28 00:00:00-delta:31|14 images
2020-05-29 00:00:00-2020-06-29 00:00:00-delta:31|14 images
2020-06-30 00:00:00-2020-07-30 00:00:00-delta:30|16 images


In [13]:
ds = np.arange(dt2)
img_collections = []
split_ds = np.array_split(ds, 12)
for i, dsi in enumerate(split_ds):
    di0 = d1 - datetime.timedelta(days=before_days) + datetime.timedelta(days=int(dsi[0]))
    di1 = d1 - datetime.timedelta(days=before_days) + datetime.timedelta(days=int(dsi[-1]))
    img_col = sar_collection.filterDate(str(di0.date()), str(di1.date()))
    img = img_col.mean().clip(roi)
    print(f'{di0}-{di1}-delta:{(di1-di0).days}|{len(img_col.getInfo()["features"])} images')
    map_view.addLayer(img, vizParams, f't2-{i:04d}')
    export_sar(img, roi, f't2_{i:04d}')

2020-06-30 00:00:00-2020-07-30 00:00:00-delta:30|16 images
2020-07-31 00:00:00-2020-08-30 00:00:00-delta:30|14 images
2020-08-31 00:00:00-2020-09-30 00:00:00-delta:30|14 images
2020-10-01 00:00:00-2020-10-31 00:00:00-delta:30|16 images
2020-11-01 00:00:00-2020-12-01 00:00:00-delta:30|10 images
2020-12-02 00:00:00-2021-01-01 00:00:00-delta:30|12 images
2021-01-02 00:00:00-2021-02-01 00:00:00-delta:30|14 images
2021-02-02 00:00:00-2021-03-03 00:00:00-delta:29|14 images
2021-03-04 00:00:00-2021-04-02 00:00:00-delta:29|12 images
2021-04-03 00:00:00-2021-05-02 00:00:00-delta:29|14 images
2021-05-03 00:00:00-2021-06-01 00:00:00-delta:29|12 images
2021-06-02 00:00:00-2021-07-01 00:00:00-delta:29|14 images


In [18]:
sar_collection = ee.ImageCollection('COPERNICUS/S2_SR').filterDate(start_date, end_date)
sar_collection = sar_collection.filterBounds(roi)

In [20]:
opt_info = sar_collection.getInfo()

In [24]:
opt_info['features']

[{'type': 'Image',
  'bands': [{'id': 'B1',
    'data_type': {'type': 'PixelType',
     'precision': 'int',
     'min': 0,
     'max': 65535},
    'dimensions': [1830, 1830],
    'crs': 'EPSG:32720',
    'crs_transform': [60, 0, 699960, 0, -60, 9200020]},
   {'id': 'B2',
    'data_type': {'type': 'PixelType',
     'precision': 'int',
     'min': 0,
     'max': 65535},
    'dimensions': [10980, 10980],
    'crs': 'EPSG:32720',
    'crs_transform': [10, 0, 699960, 0, -10, 9200020]},
   {'id': 'B3',
    'data_type': {'type': 'PixelType',
     'precision': 'int',
     'min': 0,
     'max': 65535},
    'dimensions': [10980, 10980],
    'crs': 'EPSG:32720',
    'crs_transform': [10, 0, 699960, 0, -10, 9200020]},
   {'id': 'B4',
    'data_type': {'type': 'PixelType',
     'precision': 'int',
     'min': 0,
     'max': 65535},
    'dimensions': [10980, 10980],
    'crs': 'EPSG:32720',
    'crs_transform': [10, 0, 699960, 0, -10, 9200020]},
   {'id': 'B5',
    'data_type': {'type': 'PixelType',

In [ ]:
for opt_info['features']